Tutoriel : Visualisation interactive de données électorales avec GeoPandas et Bokeh en Python

Dans ce tutoriel, nous allons apprendre à utiliser GeoPandas (pour manipuler des données géographiques) et Bokeh (pour créer des visualisations interactives) afin de représenter des résultats électoraux sur une carte de la Mauritanie.

Nous travaillerons avec :

Un fichier CSV contenant les résultats électoraux en Mauritanie (élections 2019–2024) :

   - [results_elections_rim_2019-2024.csv](https://raw.githubusercontent.com/binorassocies/rimdata/refs/heads/main/data/results_elections_rim_2019-2024.csv)
2. Un shapefile des divisions administratives (Moughataas) de Mauritanie :
   - [mrt_adm_ansade_20240327_ab_shp.zip](https://data.humdata.org/dataset/8d49f50d-92a8-46d9-9462-f821a8058f6d/resource/dacb6ad2-13b6-4f14-b1e9-44b800d76e58/download/mrt_adm_ansade_20240327_ab_shp.zip)


L’idée principale est la suivante :

GeoPandas permettra de charger le shapefile, de manipuler les géométries et de fusionner les résultats électoraux avec les limites administratives.

Bokeh servira ensuite à afficher une carte interactive, avec des fonctionnalités comme le survol (hover), le zoom, et la sélection d’un candidat.

Nous allons explorer comment :

Charger et manipuler un shapefile avec GeoPandas.

Charger les données électorales au format CSV avec Pandas.

Filtrer les données pour ne conserver que l’élection de 2024.

Fusionner les résultats électoraux avec le shapefile (par moughataa).

Visualiser les résultats sous forme de cartes interactives Bokeh et personnaliser l’affichage (couleurs, légendes, titres, etc.).

Prérequis

Python 3.x

GeoPandas (et ses dépendances)

Pandas

Bokeh

Jupyter Notebook (ou JupyterLab)

Installation
Si vous utilisez Anaconda/Miniconda :
conda install -c conda-forge geopandas bokeh

Sinon, via pip :
pip install geopandas bokeh


Remarque : GeoPandas dépend de bibliothèques système (GDAL, Fiona, Shapely…). L’installation via conda est généralement plus simple.

In [2]:
pip install geopandas bokeh

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 25.3
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
import geopandas as gpd
import pandas as pd
from pathlib import Path

# Bibliothèques Bokeh pour la visualisation interactive
from bokeh.io import output_notebook
from bokeh.plotting import figure, show

# Activer l'affichage des graphiques Bokeh dans le notebook
output_notebook()


Loading BokehJS ...

Chargement du shapefile

Le shapefile des divisions administratives de la Mauritanie peut être téléchargé depuis le lien indiqué plus haut. Après téléchargement, décompressez le fichier mrt_adm_ansade_20240327_ab_shp.zip sur votre machine. L’archive contient plusieurs fichiers (par exemple .shp, .dbf, .shx, .prj, etc.) : ensemble, ils décrivent la géométrie (polygones) et les attributs des Moughataas.

Dans ce tutoriel, nous supposons que ces fichiers ont été extraits dans un dossier data/. Nous allons charger le fichier principal .shp avec GeoPandas. Une fois les données géographiques disponibles dans un GeoDataFrame, nous pourrons ensuite les convertir en format compatible avec Bokeh afin d’afficher une carte interactive (survol, zoom, légende, etc.).

In [4]:
# Exemple : si le shapefile principal est nommé 'mrt_admbnda_adm2_20240327_AB.shp'


ROOT = Path.cwd().parent  
shapefile_path = ROOT / "mrshape" / "mrt_admbnda_adm2_ansade_20240327.shp"
gdf_moughataas = gpd.read_file(shapefile_path)

gdf_moughataas.info()


<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 63 entries, 0 to 62
Data columns (total 14 columns):
 #   Column      Non-Null Count  Dtype         
---  ------      --------------  -----         
 0   ADM2_EN     63 non-null     object        
 1   ADM2_PCODE  63 non-null     object        
 2   ADM2_REF    14 non-null     object        
 3   ADM1_EN     63 non-null     object        
 4   ADM1_PCODE  63 non-null     object        
 5   ADM0_EN     63 non-null     object        
 6   ADM0_PCODE  63 non-null     object        
 7   date        63 non-null     datetime64[ms]
 8   validOn     63 non-null     datetime64[ms]
 9   validTo     0 non-null      datetime64[ms]
 10  Shape_Leng  63 non-null     float64       
 11  Shape_Area  63 non-null     float64       
 12  AREA_SQKM   63 non-null     float64       
 13  geometry    63 non-null     geometry      
dtypes: datetime64[ms](3), float64(3), geometry(1), object(7)
memory usage: 7.0+ KB


Vous devriez obtenir un GeoDataFrame contenant plusieurs colonnes descriptives telles que ADM2_EN, ADM2_PCODE, ainsi que d’autres informations associées aux Moughataas. Repérez en particulier la colonne qui contient le nom de la Moughataa (en français, en arabe ou en transcription latine), car elle servira de clé de fusion avec les données électorales du CSV.

Par exemple, le nom de la moughataa peut se trouver dans la colonne ADM2_EN. Dans la suite, nous supposerons que ADM2_EN correspond au nom de la moughataa. Cette colonne sera utilisée pour relier les résultats électoraux aux polygones du shapefile, puis pour préparer l’affichage interactif avec Bokeh (survol, légende, sélection du candidat, etc.).

## Chargement des données CSV

Le fichier CSV results_elections_rim_2019-2024.csv contient les résultats des élections en Mauritanie pour la période 2019–2024. Nous allons le charger avec Pandas, puis filtrer les données afin de ne conserver que celles de l’élection de 2024.

Ces résultats serviront ensuite à alimenter la carte : après agrégation et fusion avec le shapefile des moughataas, nous pourrons afficher les votes sur une carte interactive avec Bokeh (survol, zoom, et sélection du candidat).

In [5]:
csv_url = "https://raw.githubusercontent.com/binorassocies/rimdata/refs/heads/main/data/results_elections_rim_2019-2024.csv"
df_elections = pd.read_csv(csv_url)

df_elections_2024 = df_elections[df_elections["year"] == 2024]
df_elections_2024.head()

year      election wilaya moughataa  commune  \
25769  2024  Presidential  Adrar   Aoujeft  Aoujeft   
25770  2024  Presidential  Adrar   Aoujeft  Aoujeft   
25771  2024  Presidential  Adrar   Aoujeft  Aoujeft   
25772  2024  Presidential  Adrar   Aoujeft  Aoujeft   
25773  2024  Presidential  Adrar   Aoujeft  Aoujeft   

                               candidate  registered_voters  nb_null_votes  \
25769                   Biram Dah  Abeid               3240             34   
25770           El Id Mohameden M’Bareck               3240             34   
25771  Hamadi Sid’El Moctar Mohamed Abdi               3240             34   
25772                   Mamadou Bocar Ba               3240             34   
25773           Mohamed Cheikh Ghazouani               3240             34   

       nb_neutral_votes  nb_votes  
25769                15       119  
25770                15       104  
25771                15       183  
25772                15         2  
25773                15      1193

Vérifiez la structure de `df_elections_2024`. Vous devriez voir des colonnes indiquant la Moughataa, le candidat, le nombre de voix, etc. Dans ce tutoriel, nous allons supposer les noms de colonnes suivants (à adapter en fonction de vos données réelles) :

- `moughataa` : le nom de la Moughataa
- `candidate` : le nom du candidat
- `nb_votes` : le nombre de voix reçues par ce candidat dans cette Moughataa
- `year` : l'année de l'élection

## Agrégation et pivot des données

Nous voulons représenter la répartition des voix par candidat et par Moughataa pour 2024. Pour cela, nous allons d’abord agréger les voix (somme) par moughataa et par candidat, puis fusionner ces résultats avec le shapefile.

### Option 1 : Carte interactive unique avec sélection du candidat (Bokeh)

Avec Bokeh, nous pouvons créer une seule carte interactive et ajouter un menu (Select) permettant de choisir un candidat. La coloration et les informations affichées (survol) se mettront alors à jour automatiquement pour le candidat sélectionné.

### Option 2 : Pivot et création d’un DataFrame large

On peut aussi créer un pivot de la forme : Moughataa en index, Candidats en colonnes, Voix en valeurs, puis fusionner avec le shapefile. Ensuite, on pourrait afficher une carte interactive pour chaque colonne/candidat, ou permettre à l’utilisateur de choisir la colonne à afficher.

Ici, nous allons illustrer la première option (carte interactive avec sélection du candidat) pour plus de lisibilité et une meilleure exploration des résultats.

Pour fusionner les données électorales avec le shapefile, on a besoin d'une clé commune. Nous allons faire correspondre la colonne du shapefile (par ex. ADM2_EN) avec la colonne moughataa du CSV, puis effectuer un merge.

> **Remarque** : Les noms de Moughataas peuvent ne pas correspondre exactement (accents, différences d'orthographe, etc.). Dans un cas réel, vous devrez peut-être normaliser ces noms (ex. tout en majuscules, enlever les accents, etc.) avant de faire la jointure.

Une fois la fusion réalisée, le GeoDataFrame contiendra à la fois :

- la géométrie des moughataas (geometry)

- et les résultats électoraux (nb_votes, candidate, etc.)

Ce GeoDataFrame fusionné pourra ensuite être converti en GeoJSON afin d'être affiché sous forme de carte interactive avec Bokeh (survol, zoom, sélection du candidat).

Pour cet exemple, nous allons supposer que les noms correspondent directement

In [6]:
# Pour faciliter, je vais renommer la colonne ADM2_EN en 'moughataa' si c'est la bonne colonne

gdf_moughataas = gdf_moughataas.rename(columns={"ADM2_EN": "moughataa"})  # À adapter selon votre shapefile
list(gdf_moughataas["moughataa"])

['Ouadane',
 'Atar',
 'Aoujeft',
 'Chinguitti',
 'Guerou',
 'Kiffa',
 'Boumdeid',
 'Kankoussa',
 'Barkéol',
 'Magtalahjar',
 'Bababé',
 'Maal',
 'M’Bagne',
 'Aleg',
 'Boghé',
 'Nouadhibou',
 'Chami',
 'Kaedi',
 'M’Bout',
 'Lexeibe 1',
 'Maghama',
 'Mounguel',
 'Wompou',
 'Sélibaby',
 'Ghabou',
 'Ould Yengé',
 'Djiguenni',
 'Adel Bagrou',
 'Oualata',
 'N’Beiket Lehwach',
 'Timbédra',
 'Bassiknou',
 'Néma',
 'Amourj',
 'Tamchekett',
 'Aïoun',
 'Kobeni',
 'Touil',
 'Tintane',
 'Bennechab',
 'Akjoujt',
 'Toujounine',
 'Dar Naïm',
 'Teyarett',
 'Sebkha',
 'Ksar',
 'Tevragh Zeina',
 'Arafat',
 'El Mina',
 'Riad',
 'Moudjeria',
 'Tichit',
 'Tidjikja',
 'Bir Moughrein',
 'Zoueirat',
 'F’Deirick',
 'Tekane',
 'Boutilimit',
 'Keur Macen',
 'Ouad Naga',
 'Mederdra',
 'R’Kiz',
 'Rosso']

Ensuite, nous allons regrouper les données de 2024 par moughataa et candidate afin d’obtenir, pour chaque candidat et chaque moughataa, la somme des voix (si nécessaire). Ces résultats agrégés pourront ensuite être fusionnés avec le shapefile et utilisés pour alimenter la carte interactive avec Bokeh (survol, zoom, sélection du candidat).

In [7]:
# Agrégation des voix par Moughataa et par candidat
df_agg_2024 = df_elections_2024.groupby(["moughataa", "candidate"], as_index=False)["nb_votes"].sum()
df_agg_2024.head()

moughataa                          candidate  nb_votes
0  Adel Bagrou                   Biram Dah  Abeid       755
1  Adel Bagrou           El Id Mohameden M’Bareck        79
2  Adel Bagrou  Hamadi Sid’El Moctar Mohamed Abdi       562
3  Adel Bagrou                   Mamadou Bocar Ba        24
4  Adel Bagrou           Mohamed Cheikh Ghazouani      9757

### Visualisation pour chaque candidat

1. Lister les candidats disponibles en 2024.
2. Sélectionner un candidat (à partir de cette liste) et filtrer df_agg_2024.
3. Fusionner les résultats filtrés avec gdf_moughataas (par moughataa).
4. Afficher une carte interactive avec Bokeh, où la coloration dépend du nombre de voix et où le survol permet de consulter les valeurs.

Ensuite, nous verrons comment personnaliser l’apparence de la carte (palette de couleurs, légende, titre, informations affichées au survol, etc.).

In [9]:
# Liste unique des candidats en 2024
candidats_2024 = df_agg_2024["candidate"].unique()
candidats_2024

array(['Biram Dah  Abeid', 'El Id Mohameden M’Bareck',
       'Hamadi Sid’El Moctar Mohamed Abdi', 'Mamadou Bocar Ba',
       'Mohamed Cheikh Ghazouani', 'Mohamed Lemine El Mourteji  El Wavi',
       'Outouma Antoine Souleymane Soumaré'], dtype=object)

#### Boucle sur les candidats

In [8]:
# ==========================================
# Carte interactive Bokeh (Notebook)
# Échelle commune pour tous les candidats
# Palette verte inversée : foncé en haut, clair en bas
# Solution 1 : garder uniquement moughataa, nb_votes, geometry
# ==========================================

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import GeoJSONDataSource, LinearColorMapper, ColorBar, HoverTool, Select, CustomJS
from bokeh.layouts import column
from bokeh.palettes import Greens9  # ✅ Palette verte

output_notebook()

# ----------------------------------------------------------
# 1) Liste des candidats
# ----------------------------------------------------------
candidats_2024 = list(df_agg_2024["candidate"].unique())

# ----------------------------------------------------------
# 2) Préparer un GeoJSON pour chaque candidat (à l'avance)
# ----------------------------------------------------------
geojson_dict = {}

for cand in candidats_2024:
    df_cand = df_agg_2024[df_agg_2024["candidate"] == cand].copy()

    gdf_tmp = gdf_moughataas.merge(df_cand, on="moughataa", how="left")
    gdf_tmp["nb_votes"] = gdf_tmp["nb_votes"].fillna(0)

    # Solution 1 : garder uniquement les colonnes utiles (évite Timestamp)
    gdf_tmp = gdf_tmp[["moughataa", "nb_votes", "geometry"]].copy()

    geojson_dict[cand] = gdf_tmp.to_json()

# Candidat par défaut (premier de la liste)
candidat_default = candidats_2024[0]

# Source initiale
geosource = GeoJSONDataSource(geojson=geojson_dict[candidat_default])

# ----------------------------------------------------------
# 3) Échelle globale (commune) pour tous les candidats
# ----------------------------------------------------------
global_min = float(df_agg_2024["nb_votes"].min())
global_max = float(df_agg_2024["nb_votes"].max())

# éviter le cas global_min == global_max
if global_min == global_max:
    global_max = global_min + 1

# ----------------------------------------------------------
# 4) Palette verte inversée : foncé en haut, clair en bas
# ----------------------------------------------------------
palette_inverse = Greens9[::-1]  # ✅ Vert inversé

color_mapper = LinearColorMapper(
    palette=palette_inverse,
    low=global_min,
    high=global_max
)

# ----------------------------------------------------------
# 5) Figure Bokeh
# ----------------------------------------------------------
p = figure(
    title=f"Résultats {candidat_default} - Élection 2024",
    width=900,
    height=600,
    tools="pan,wheel_zoom,reset,save",
    active_scroll="wheel_zoom"
)

patches = p.patches(
    "xs", "ys",
    source=geosource,
    fill_color={"field": "nb_votes", "transform": color_mapper},
    line_color="black",
    line_width=0.5,
    fill_alpha=0.8
)

# Hover
hover = HoverTool(
    renderers=[patches],
    tooltips=[
        ("Moughataa", "@moughataa"),
        ("Voix", "@nb_votes{0,0}")
    ]
)
p.add_tools(hover)

# ColorBar (légende) - restera aussi inversée
color_bar = ColorBar(
    color_mapper=color_mapper,
    label_standoff=12,
    location=(0, 0),
    title="Nombre de voix"
)
p.add_layout(color_bar, "right")

# ----------------------------------------------------------
# 6) Select + callback JS (mise à jour de la carte uniquement)
# ----------------------------------------------------------
select = Select(
    title="Choisir un candidat :",
    value=candidat_default,
    options=candidats_2024
)

callback = CustomJS(
    args=dict(
        geosource=geosource,
        geojson_dict=geojson_dict,
        p=p
    ),
    code="""
        const cand = cb_obj.value;

        // Mettre à jour la carte (GeoJSON)
        geosource.geojson = geojson_dict[cand];

        // Mettre à jour le titre
        p.title.text = `Résultats ${cand} - Élection 2024`;
    """
)

select.js_on_change("value", callback)

# ----------------------------------------------------------
# 7) Affichage final
# ----------------------------------------------------------
layout = column(select, p)
show(layout)


Loading BokehJS ...